In [75]:
import os
import json
from collections import defaultdict,Counter

In [82]:
import re
import string
def normalize_answer(s):    
    def remove_(text):
        ''' 불필요한 기호 제거 '''
        text = re.sub("'", " ", text)
        text = re.sub('"', " ", text)
        text = re.sub('《', " ", text)
        text = re.sub('》', " ", text)
        text = re.sub('<', " ", text)
        text = re.sub('>', " ", text) 
        text = re.sub('〈', " ", text)
        text = re.sub('〉', " ", text)   
        text = re.sub("\(", " ", text)
        text = re.sub("\)", " ", text)
        text = re.sub("‘", " ", text)
        text = re.sub("’", " ", text)      
        text = re.sub("/n", " ", text)      
        return ' '.join(text.split())

    def white_space_fix(text):
        return 

    # def remove_punc(text):
    #     exclude = set(string.punctuation)
    #     return ''.join(ch for ch in text if ch not in exclude)

    return remove_(s)

In [93]:
file_path ='./nbest'                                  #소프트보팅 할 nbest_predictions.json들 있는 경로
n=20                                                  #nbest prediction -> 개수확인 필요
json_file_path = []
json_files=[]
for json_path in os.listdir(file_path):
    if json_path.endswith('.json'):
        print(json_path)                    
        json_file_path.append(json_path)

for file in json_file_path:
    fp=os.path.join(file_path,file)
    with open(fp,"r",encoding='utf-8') as json_file:
        json_data=json.load(json_file)
        json_files.append(json_data)

yeom_nbest_predictions.json
nbest_predictions_8_roberta-large_korquad-1_EM_61.25.json
wook_nbest_predictions.json
inni_nbest_predictions.json


염 : 	62.5000
동 :   61.25
인 :   62.5
제 :   62.5
한성 : 49.58

In [8]:
from torch.nn import functional as F
import torch
em_list = [62.5,61.25,62.5,62.5]           #이 부분이 EM인데 EM 전체적으로 차이가 없드라구요. 그래서 제거 EM하나 추가해봤었는뎁
tt = torch.FloatTensor(em_list)
tt = F.softmax(tt).to('cpu').numpy().tolist()
# a = [i/sum(em_list) for i in em_list]      # EM의 비율을 넣고 싶어서 합산하고 평균 냈어요!! ㅇㅋ?ㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋㅋ
# em_list = a                                         # em soft_voting
# em_list

/tmp/ipykernel_16661/3495430465.py:5: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  tt = F.softmax(tt).to('cpu').numpy().tolist()


In [9]:
tt

[0.30427461862564087,
 0.0871761366724968,
 0.30427461862564087,
 0.30427461862564087]

In [101]:
json_files[0]['mrc-1-000653'][0]['text']

'사만(サマーン)'

In [120]:
key_list=list(json_files[0].keys())                   # predictions.json의 key값들 설정
bin=defaultdict(list)                                 # 확률값들을 담을 dict생성-> value : list
bin2 = {}
answer_dict=defaultdict(list)                         # 최종 답변을 넣을 dict 생성 -> value : list

for i in range(len(key_list)):                        #defaultdict : key만 선언하면 value는 '' 빈 값
    bin[key_list[i]]                                 
    answer_dict[key_list[i]]

for idx,json_file in enumerate(json_files):                          # N개의 nbest_predictions 파일들
    for kl in key_list:                               # 600개의 key
        for i in range(n):                            # nbest_size : 20     
            if json_file[kl][i]['text'] in bin2.keys():
                bin2[json_file[kl][i]['text']].append(json_file[kl][i]['probability'] * em_list[idx])
                bin[kl].append({json_file[kl][i]['text'] :bin2[json_file[kl][i]['text']]})   # 그걸 여기에 넣었어요       더하는 방식과 곱하는 방식
            else:
                bin2[json_file[kl][i]['text']] = [json_file[kl][i]['probability'] * em_list[idx]]
                bin[kl].append({json_file[kl][i]['text'] :bin2[json_file[kl][i]['text']]})
            # 있는데 곱하는 걸로 하니 올랐어요!              
            # bin[kl].append((normalize_answer(json_file[kl][i]['text']),json_file[kl][i]['probability']*em_list[idx]))    #@@@@@@후처리 함수 적용@@@@@
                #@@@@@@@@후처리 함수 적용 후 소프트보팅 하려면 위 코드 주석해제 후 바로위 코드 주석처리 (위의 korquad 후처리 함수) @@@@@@

In [123]:
bin.values

<function defaultdict.values>

In [125]:
bin.items()

dict_items([('mrc-1-000653', [{'사만(サマーン)': [0.10765497408919597, 0.0014831504630084015, 0.0010974443138544283, 0.0008247605520277166, 0.004658147917320979, 0.0020185307641724243]}, {'사만': [0.06631055668969849, 0.0004950480245465609, 0.00047923332482726125, 2.6852042231727484e-05, 0.05371277775596734, 0.00045532437425162926, 7.030053354387907e-06, 0.15789396199748743, 0.003661342601680276, 0.0019255594991559359, 0.0003603834602701005, 0.010911184339667085, 0.004711822049701633, 0.001995527564580716, 0.0007087860874195194]}, {'외계행성 사만(サマーン)': [0.042509912845477386, 0.0005537157681719143, 0.0007169330539415829]}, {'외계행성 사만': [0.02617764113536432, 0.00016954316565738852, 0.00031078281115047893, 0.00027963264503670697, 0.001680192036844378]}, {'별하늘계의 변경에 위치한 외계행성 사만(サマーン)': [0.0019562304319448807]}, {'사만(サマーン) 출신': [0.0014539939075259108]}, {'별하늘계의 변경에 위치한 외계행성 사만': [0.0012047925786157349]}, {'사만(サマーン) 출신의 여자아이. 지구 나이로는 13살 밖에 안된 어린 소녀의 모습이지만 사만': [0.0010389778482255024, 6.340256887464668e-

In [80]:
for kl in key_list:                                   # 600개의 키
    answer_hubo={}
    for i in range(len(bin[kl])):                  
        if bin[kl][i][0] not in answer_hubo.keys():   # 빈 객체에서 없다면 key 추가
            answer_hubo[bin[kl][i][0]]=bin[kl][i][1]
        else:
            answer_hubo[bin[kl][i][0]]+=bin[kl][i][1] # 있다면 확률값 더하기 -> 이렇게 하지 않으면 dictionary는 자동으로 중복제거(set)
    max_answer=max(answer_hubo.keys(),key= lambda prob : answer_hubo[prob])     #최대 확률값을 답변으로
    answer_dict[kl]=max_answer

In [81]:
new_nbest_json_path = "./nbest/nbest_ensemble.json"           # nbest_ensemble.json 저장

with open(new_nbest_json_path, 'w', encoding='utf-8') as file:
    json.dump(answer_dict, file)

In [1]:
for key, val in x:
    answer_dict[kl].append({'text': key, 'probability' : val})

SyntaxError: unexpected EOF while parsing (3029447340.py, line 1)

In [ ]:
x=sorted(calculate.keys(),key= lambda prob : answer_hubo[prob])[:20]     #최대 확률값을 답변으로
